In [1]:
# =============================================================================
# CONFIGURATION - Change these values to control the extraction
# =============================================================================

# --- Model Selection ---
MODEL_PROVIDER = "openai"           # "gemini" or "openai"
GEMINI_MODEL = "gemini-2.5-flash"   # gemini-2.5-flash (65K output), gemini-2.5-pro
OPENAI_MODEL = "gpt-4o-mini"        # gpt-4o-mini, gpt-4o, gpt-4.1-nano, gpt-4.1

# --- Input Selection ---
ACCESSION_NO = "0001571996-25-000096"  # 8-K accession number from Neo4j
SAMPLE_FILE_PATH = None                 # Or set local file path (overrides Neo4j)

# --- Catalog Options ---
INCLUDE_AMENDMENTS = False              # Include 10-K/A, 10-Q/A amendments
MAX_CONCEPTS_WITH_HISTORY = None        # None = all concepts, or int like 100
MAX_HISTORY_PER_CONCEPT = 5          # None = all history, or int like 4 (recent quarters)
CONTEXT_BUDGET_CHARS = None             # None = unlimited, or int like 100000
INCLUDE_RELATIONSHIPS = True            # Include calc/presentation networks

# --- Extraction Options ---
MAX_CHAR_BUFFER = 4000                  # Chunk size for 8-K document
DEBUG_MODE = True                       # Show raw LLM output before parsing
SUPPRESS_PARSE_ERRORS = False           # Suppress JSON parse errors

# =============================================================================
# Provider-specific configurations (auto-selected based on MODEL_PROVIDER)
# 
# NOTE on max_output_tokens:
#   - Gemini: Supports max_output_tokens (65K for gemini-2.5-flash)
#   - OpenAI: Newer models (gpt-4o-mini, o1, etc.) use max_completion_tokens
#             but LangExtract only supports max_tokens. Set to None to use
#             model defaults and avoid parameter errors.
# =============================================================================
PROVIDER_CONFIG = {
    "gemini": {
        "max_workers": 5,           # Lower due to stricter rate limits
        "batch_length": 5,
        "max_output_tokens": 65536, # gemini-2.5-flash supports 65K
    },
    "openai": {
        "max_workers": 10,           # Higher rate limits
        "batch_length": 5,
        "max_output_tokens": None,  # Don't pass - use model default (avoids max_tokens vs max_completion_tokens issue)
    }
}

# Derived values (don't change these)
model_name = GEMINI_MODEL if MODEL_PROVIDER == "gemini" else OPENAI_MODEL

# =============================================================================
print(f"Provider: {MODEL_PROVIDER}")
print(f"Model: {model_name}")
print(f"Input: {ACCESSION_NO or SAMPLE_FILE_PATH}")

Provider: openai
Model: gpt-4o-mini
Input: 0001571996-25-000096


In [2]:
# Setup: Add paths, load environment, and imports
import sys
import os

# Load .env file (so you don't need to export keys)
from dotenv import load_dotenv
load_dotenv("/home/faisal/EventMarketDB/.env")

# Verify API keys are loaded
if MODEL_PROVIDER == "gemini":
    assert os.getenv("GEMINI_API_KEY"), "GEMINI_API_KEY not found in .env"
    print("✓ GEMINI_API_KEY loaded")
elif MODEL_PROVIDER == "openai":
    assert os.getenv("OPENAI_API_KEY"), "OPENAI_API_KEY not found in .env"
    print("✓ OPENAI_API_KEY loaded")

# Ensure imports resolve
sys.path.insert(0, os.getcwd())

# Core imports
from xbrl_catalog import get_xbrl_catalog, print_catalog_summary, get_neo4j_driver

print(f"Working directory: {os.getcwd()}")

✓ OPENAI_API_KEY loaded
Working directory: /home/faisal/EventMarketDB/drivers/8K_XBRL_Linking/FinalScripts


## Status Determination

Determines extraction status based on validation results:
- **COMMITTED**: confidence ≥ 0.90 + valid qname + valid unit + valid period + value parsed
- **CANDIDATE_ONLY**: Valid but low confidence or UNMATCHED concept  
- **REVIEW**: Parse failure, invalid period, or invalid unit

---
## Catalog Fetch (Neo4j)

Fetches XBRL catalog from Neo4j (READ ONLY - no writes). Contains concepts, units, dimensions, and historical facts for context.

In [3]:
# Fetch 8-K metadata and XBRL catalog from Neo4j
# ============================================================================
# This cell:
# 1. Gets 8-K Report metadata (CIK, created datetime, text content)
# 2. Uses the 8-K's created datetime as as_of_dt for temporal filtering
# 3. Fetches XBRL catalog with only filings BEFORE the 8-K was filed
# ============================================================================

driver = get_neo4j_driver()

with driver.session() as session:
    # Fetch 8-K report metadata
    result = session.run("""
        MATCH (r:Report {accessionNo: $accession_no})
        MATCH (r)-[:PRIMARY_FILER]->(c:Company)
        RETURN r.accessionNo as accession_no,
               r.formType as form_type,
               r.created as created,
               r.periodOfReport as period_of_report,
               r.exhibit_contents as exhibit_contents,
               c.cik as cik,
               c.ticker as ticker,
               c.name as company_name
    """, accession_no=ACCESSION_NO)
    
    report = result.single()
    
    if not report:
        raise ValueError(f"Report {ACCESSION_NO} not found in Neo4j")

# Extract 8-K metadata
report_cik = report["cik"]
report_ticker = report["ticker"]
report_created = report["created"]  # This is our as_of_dt!
report_exhibits = report["exhibit_contents"]

print(f"8-K Report: {ACCESSION_NO}")
print(f"Company: {report['company_name']} ({report_ticker})")
print(f"CIK: {report_cik}")
print(f"Filed: {report_created}")
print(f"Period: {report['period_of_report']}")

# Handle exhibit_contents - can be string or dict
if isinstance(report_exhibits, str):
    # It's already the 8-K text content
    sample_8k_text = report_exhibits
    print(f"8-K text: {len(sample_8k_text):,} characters")
elif isinstance(report_exhibits, dict):
    # It's a dict of exhibit_name -> content
    sample_8k_text = "\n\n".join([
        f"=== {name} ===\n{content}" 
        for name, content in report_exhibits.items()
    ])
    print(f"8-K text: {len(sample_8k_text):,} characters from {len(report_exhibits)} exhibits")
else:
    sample_8k_text = None
    print("Warning: No exhibit_contents found. Use SAMPLE_FILE_PATH instead.")

# Fetch XBRL catalog with as_of_dt = 8-K's created datetime
# This ensures we only get XBRL from filings BEFORE the 8-K was filed
print(f"\nFetching XBRL catalog with as_of_dt={report_created}...")

catalog = get_xbrl_catalog(
    cik=report_cik,
    as_of_dt=report_created,
    include_amendments=INCLUDE_AMENDMENTS,
    include_relationships=True,
    driver=driver
)

print_catalog_summary(catalog)

8-K Report: 0001571996-25-000096
Company: DELL TECHNOLOGIES INC (DELL)
CIK: 0001571996
Filed: 2025-08-28T16:09:59-04:00
Period: 2025-08-28
8-K text: 29,249 characters

Fetching XBRL catalog with as_of_dt=2025-08-28T16:09:59-04:00...

XBRL Catalog: DELL TECHNOLOGIES INC (DELL)
CIK: 0001571996
Industry: ComputerHardware
Sector: Technology

Total Filings: 10
Total Facts: 16,517
Unique Concepts: 814

Filings:
  - 10-Q (2025-05-02): 1,160 facts
  - 10-K (2025-01-31): 2,185 facts
  - 10-Q (2024-11-01): 1,565 facts
  - 10-Q (2024-08-02): 1,541 facts
  - 10-Q (2024-05-03): 1,194 facts
  - 10-K (2024-02-02): 2,044 facts
  - 10-Q (2023-11-03): 1,728 facts
  - 10-Q (2023-08-04): 1,673 facts
  - 10-Q (2023-05-05): 1,316 facts
  - 10-K (2023-02-03): 2,111 facts

Top Segments:
  - FinanceLeasesPortfolioSegment: 811 facts
  - LoansAndFinanceReceivables: 707 facts
  - Nondesignated: 590 facts
  - UnsecuredDebt: 576 facts
  - ForeignExchangeContract: 528 facts




In [4]:
# Inspect catalog data
if 'catalog' in dir():
    print(f"Valid Qnames ({len(catalog.concepts)} total, first 20):")
    for qname in list(catalog.concepts.keys())[:20]:
        print(f"  {qname}")
    
    print(f"\nValid Units ({len(catalog.units)} total):")
    for unit in catalog.units.keys():
        print(f"  {unit}")

Valid Qnames (814 total, first 20):
  us-gaap:Revenues
  us-gaap:StockholdersEquityIncludingPortionAttributableToNoncontrollingInterest
  us-gaap:NotesReceivableGross
  us-gaap:DebtInstrumentCarryingAmount
  us-gaap:DerivativeFairValueOfDerivativeLiability
  us-gaap:DerivativeFairValueOfDerivativeAsset
  us-gaap:CostOfRevenue
  us-gaap:ProfitLoss
  us-gaap:DerivativeAssetsLiabilitiesAtFairValueNet
  us-gaap:OperatingIncomeLoss
  us-gaap:DebtInstrumentInterestRateStatedPercentage
  us-gaap:NotesReceivableNet
  us-gaap:LongTermDebt
  us-gaap:CommonStockSharesIssued
  us-gaap:FinancingReceivableAllowanceForCreditLosses
  us-gaap:DividendsCommonStock
  us-gaap:FinancingReceivableRevolving
  us-gaap:AdjustmentsToAdditionalPaidInCapitalSharebasedCompensationRequisiteServicePeriodRecognitionValue
  us-gaap:SeveranceCosts1
  us-gaap:OperatingExpenses

Valid Units (12 total):
  iso4217:USD
  shares
  pure
  iso4217:USDshares
  dell:vote
  iso4217:EUR
  dell:facility
  dell:segment
  dell:tranch

In [5]:
# Preview and export catalog
# ============================================================================
# View LLM context (text format) and optionally export to HTML
# ============================================================================

if 'catalog' in dir():
    # Generate LLM context using config from Cell 0
    context = catalog.to_llm_context(
        max_concepts_with_history=MAX_CONCEPTS_WITH_HISTORY,
        max_history_per_concept=MAX_HISTORY_PER_CONCEPT,
        max_sample_facts=None,  # Section currently disabled
        include_relationships=INCLUDE_RELATIONSHIPS,
        context_budget_chars=CONTEXT_BUDGET_CHARS
    )
    print(f"LLM Context ({len(context):,} chars):\n")
    print(context[:3000])
    print("\n... [truncated] ...")
    
    # Export to HTML for full catalog review
    html_output = f"/home/faisal/EventMarketDB/drivers/8K_XBRL_Linking/output/{report_ticker}_catalog.html"
    catalog.to_html(output_path=html_output)
    print(f"\nOpen in browser: file://{html_output}")

LLM Context (157,554 chars):

<<<BEGIN_XBRL_REFERENCE_DATA>>>
COMPANY: DELL TECHNOLOGIES INC (DELL)
CIK: 0001571996 | Industry: ComputerHardware | Sector: Technology

LEGEND:
• qname = unique concept identifier (e.g., us-gaap:Revenues)
• label = human-readable name

────────────────────────────────────────────────────────────────────────
FISCAL CALENDAR
────────────────────────────────────────────────────────────────────────
Fiscal Year End: January 31
Quarter Mapping (fiscal → calendar end month):
  FY2026: Q1→Apr25 | Q2→Jul25 | Q3→Oct25 | Q4→Jan26
  FY2025: Q1→Apr24 | Q2→Jul24 | Q3→Oct24 | Q4→Jan25

────────────────────────────────────────────────────────────────────────
CONCEPTS (433 numeric, top 433 shown)
History shows recent values for magnitude validation (10-K=annual, 10-Q=quarterly)
────────────────────────────────────────────────────────────────────────
── TOP CONCEPTS (with history for magnitude validation) ──
us-gaap:NotesReceivableGross | Financing Receivable, before Allow

In [6]:
# Alternative: Load 8-K from file (if not using Neo4j fetch above)
# ============================================================================
if SAMPLE_FILE_PATH and not report_exhibits:
    print(f"Loading 8-K from file: {SAMPLE_FILE_PATH}")
    with open(SAMPLE_FILE_PATH, 'r') as f:
        sample_8k_text = f.read()
    print(f"Loaded 8-K: {len(sample_8k_text):,} characters")

# Build catalog context for LLM using config from Cell 0
llm_context = catalog.to_llm_context(
    max_concepts_with_history=MAX_CONCEPTS_WITH_HISTORY,
    max_history_per_concept=MAX_HISTORY_PER_CONCEPT,
    max_sample_facts=None,  # Section currently disabled
    include_relationships=INCLUDE_RELATIONSHIPS,
    context_budget_chars=CONTEXT_BUDGET_CHARS
)

print(f"Catalog context: {len(llm_context):,} characters")
print(f"8-K text: {len(sample_8k_text):,} characters")
print(f"Total context: {len(llm_context) + len(sample_8k_text):,} characters")

Catalog context: 157,554 characters
8-K text: 29,249 characters
Total context: 186,803 characters


In [7]:
# Import extraction functions from extractor.py
from extractor import extract_facts_debug, CatalogContext

print("✓ Imported extract_facts_debug from extractor.py")

✓ Imported extract_facts_debug from extractor.py


In [8]:
# Run extraction using extractor.py
print("Running extraction...")
print(f"Provider: {MODEL_PROVIDER}")
print(f"Model: {model_name}")

# Get provider-specific config
cfg = PROVIDER_CONFIG[MODEL_PROVIDER]
print(f"Config: max_workers={cfg['max_workers']}, batch_length={cfg['batch_length']}, max_output_tokens={cfg['max_output_tokens']}")

# Call extract_facts_debug to get both result and annotated_doc
result, annotated_doc = extract_facts_debug(
    text=sample_8k_text,
    catalog=catalog,
    filing_id=ACCESSION_NO,
    model=model_name,
    max_workers=cfg["max_workers"],
    batch_length=cfg["batch_length"],
    max_output_tokens=cfg["max_output_tokens"],
    max_char_buffer=MAX_CHAR_BUFFER,
    suppress_parse_errors=SUPPRESS_PARSE_ERRORS,
    debug=DEBUG_MODE,
)

# For inspection in Cell 10
raw_extractions = annotated_doc.extractions or []
processed_facts = result.facts

print(f"\n✓ {len(raw_extractions)} raw extractions from LangExtract")
print(f"✓ {result.committed_count} committed, {result.candidate_count} candidates, {result.review_count} review")

/home/faisal/EventMarketDB/venv/lib/python3.11/site-packages/langextract/extraction.py:199: UserWarning: batch_length (5) < max_workers (10). Only 5 workers will be used. Set batch_length >= max_workers for optimal parallelization.
  warnings.warn(
DEBUG:absl:Registered provider langextract.providers.gemini:GeminiLanguageModel with patterns ['^gemini'] at priority 10
DEBUG:absl:Registered provider langextract.providers.ollama:OllamaLanguageModel with patterns ['^gemma', '^llama', '^mistral', '^mixtral', '^phi', '^qwen', '^deepseek', '^command-r', '^starcoder', '^codellama', '^codegemma', '^tinyllama', '^wizardcoder', '^gpt-oss', '^meta-llama/[Ll]lama', '^google/gemma', '^mistralai/[Mm]istral', '^mistralai/[Mm]ixtral', '^microsoft/phi', '^Qwen/', '^deepseek-ai/', '^bigcode/starcoder', '^codellama/', '^TinyLlama/', '^WizardLM/'] at priority 10
DEBUG:absl:Registered provider langextract.providers.openai:OpenAILanguageModel with patterns ['^gpt-4', '^gpt4\\.', '^gpt-5', '^gpt5\\.'] at prio

Running extraction...
Provider: openai
Model: gpt-4o-mini
Config: max_workers=10, batch_length=5, max_output_tokens=None


DEBUG:absl:Skipping duplicate registration for langextract.providers.gemini:GeminiLanguageModel with patterns ['^gemini'] at priority 10
INFO:absl:Loaded provider plugin: gemini
DEBUG:absl:Skipping duplicate registration for langextract.providers.ollama:OllamaLanguageModel with patterns ['^gemma', '^llama', '^mistral', '^mixtral', '^phi', '^qwen', '^deepseek', '^command-r', '^starcoder', '^codellama', '^codegemma', '^tinyllama', '^wizardcoder', '^gpt-oss', '^meta-llama/[Ll]lama', '^google/gemma', '^mistralai/[Mm]istral', '^mistralai/[Mm]ixtral', '^microsoft/phi', '^Qwen/', '^deepseek-ai/', '^bigcode/starcoder', '^codellama/', '^TinyLlama/', '^WizardLM/'] at priority 10
INFO:absl:Loaded provider plugin: ollama
DEBUG:absl:Skipping duplicate registration for langextract.providers.openai:OpenAILanguageModel with patterns ['^gpt-4', '^gpt4\\.', '^gpt-5', '^gpt5\\.'] at priority 10
INFO:absl:Loaded provider plugin: openai
/home/faisal/EventMarketDB/venv/lib/python3.11/site-packages/langextra

✓ Extracted 29 entities (1 unique types)
  • Time: 209.79s
  • Speed: 139 chars/sec
  • Chunks: 8

✓ 29 raw extractions from LangExtract
✓ 25 committed, 4 candidates, 0 review


In [9]:
# Inspect RAW LangExtract output (before postprocessing)
print(f"RAW LANGEXTRACT OUTPUT ({len(raw_extractions)} extractions)\n" + "="*70)

for i, ext in enumerate(raw_extractions, 1):
    print(f"\n[{i}] Raw Extraction")
    print(f"    class: {ext.extraction_class}")
    print(f"    text: \"{ext.extraction_text[:80]}...\"" if len(ext.extraction_text) > 80 else f"    text: \"{ext.extraction_text}\"")
    
    # Handle char_interval (can be None)
    if ext.char_interval:
        print(f"    span: {ext.char_interval.start_pos} - {ext.char_interval.end_pos}")
    else:
        print(f"    span: N/A")
    
    if ext.alignment_status:
        print(f"    alignment: {ext.alignment_status.value}")
    
    attrs = ext.attributes or {}
    if attrs:
        print(f"    --- Attributes ---")
        for k, v in attrs.items():
            if v is not None:
                print(f"    {k}: {v}")

RAW LANGEXTRACT OUTPUT (29 extractions)

[1] Raw Extraction
    class: financial_fact
    text: "record revenue of $29.8 billion"
    span: 363 - 394
    alignment: match_exact
    --- Attributes ---
    concept_top1: us-gaap:Revenues
    matched_period: 2025-04-01→2025-06-30
    matched_unit: USD
    confidence: 0.93
    reasoning: Company-wide revenue for the quarter explicitly stated; matches standard catalog concept.

[2] Raw Extraction
    class: financial_fact
    text: "Operating income of $1.8 billion"
    span: 424 - 456
    alignment: match_exact
    --- Attributes ---
    concept_top1: us-gaap:OperatingIncomeLoss
    matched_period: 2025-04-01→2025-06-30
    matched_unit: USD
    confidence: 0.95
    reasoning: Clear operating income figure provided; matches standard catalog concept.

[3] Raw Extraction
    class: financial_fact
    text: "Diluted earnings per share (EPS) of $1.70"
    span: 541 - 582
    alignment: match_exact
    --- Attributes ---
    concept_top1: us-gaa

---
## 9. Postprocess Real Extractions

Runs the postprocessor on actual LangExtract output:
1. Filters extractions pointing into catalog context (precision fix)
2. Validates qnames, units, periods
3. Parses numeric values deterministically
4. Assigns status: COMMITTED / CANDIDATE_ONLY / REVIEW

In [10]:
# Mapping and postprocessing already done by extract_facts_debug()
# processed_facts contains the final ProcessedFact objects
# raw_extractions contains the original LangExtract output for inspection

print(f"Processed {len(processed_facts)} facts from {len(raw_extractions)} raw extractions")

Processed 29 facts from 29 raw extractions


In [11]:
# Display processed facts (already computed by extract_facts_debug)
from extraction_schema import ExtractionStatus

print(f"PROCESSED FACTS ({len(processed_facts)} total)\n" + "="*70)

for i, fact in enumerate(processed_facts, 1):
    status_icon = "✓" if fact.status == ExtractionStatus.COMMITTED else "○" if fact.status == ExtractionStatus.CANDIDATE_ONLY else "✗"
    print(f"\n[{i}] {status_icon} {fact.status.value}")
    print(f"    Text: \"{fact.extraction_text[:60]}...\"" if len(fact.extraction_text) > 60 else f"    Text: \"{fact.extraction_text}\"")
    print(f"    Concept: {fact.concept_top1}")
    if fact.concept_top2:
        print(f"    Concept2: {fact.concept_top2}")
    print(f"    Value: {fact.value_parsed:,.2f}" if fact.value_parsed else f"    Value: None")
    print(f"    Period: {fact.matched_period}")
    print(f"    Unit: {fact.matched_unit} (valid={fact.unit_valid})")
    print(f"    Confidence: {fact.confidence:.2f}")
    if fact.parse_error:
        print(f"    Parse Error: {fact.parse_error}")

print(f"\n" + "="*70)
print(f"SUMMARY: {result.committed_count} COMMITTED | {result.candidate_count} CANDIDATES | {result.review_count} REVIEW")

PROCESSED FACTS (29 total)

[1] ✓ COMMITTED
    Text: "record revenue of $29.8 billion"
    Concept: us-gaap:Revenues
    Value: 29,800,000,000.00
    Period: 2025-04-01→2025-06-30
    Unit: USD (valid=True)
    Confidence: 0.93

[2] ✓ COMMITTED
    Text: "Operating income of $1.8 billion"
    Concept: us-gaap:OperatingIncomeLoss
    Value: 1,800,000,000.00
    Period: 2025-04-01→2025-06-30
    Unit: USD (valid=True)
    Confidence: 0.95

[3] ✓ COMMITTED
    Text: "Diluted earnings per share (EPS) of $1.70"
    Concept: us-gaap:EarningsPerShareDiluted
    Value: 1.70
    Period: 2025-04-01→2025-06-30
    Unit: USD/share (valid=True)
    Confidence: 0.95

[4] ○ CANDIDATE_ONLY
    Text: "Cash flow from operations of $2.5 billion"
    Concept: UNMATCHED
    Value: 2,500,000,000.00
    Period: 2025-04-01→2025-06-30
    Unit: USD (valid=True)
    Confidence: 0.30

[5] ✓ COMMITTED
    Text: "Net income of $1.164 billion"
    Concept: us-gaap:NetIncomeLoss
    Value: 1,164,000,000.00
    Peri

---
## 10. Save Extraction Results

Saves extractions in two formats:
- **JSONL**: Raw machine-readable format with all extraction data
- **HTML**: Interactive visualization with entity highlighting in source context

In [12]:
# Output directory
import os
from datetime import datetime

OUTPUT_DIR = "/home/faisal/EventMarketDB/drivers/8K_XBRL_Linking/output"
os.makedirs(OUTPUT_DIR, exist_ok=True)

# Generate timestamp for filenames
timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
base_name = f"DELL_8K_{timestamp}"

print(f"Output directory: {OUTPUT_DIR}")
print(f"Base filename: {base_name}")

Output directory: /home/faisal/EventMarketDB/drivers/8K_XBRL_Linking/output
Base filename: DELL_8K_20251228_100308


In [13]:
# Save annotated document to JSONL using LangExtract's built-in function
import langextract as lx

jsonl_path = os.path.join(OUTPUT_DIR, f"{base_name}.jsonl")

# save_annotated_documents expects an iterator of AnnotatedDocument
lx.io.save_annotated_documents(
    annotated_documents=[annotated_doc],  # List of AnnotatedDocument
    output_dir=OUTPUT_DIR,
    output_name=f"{base_name}.jsonl"
)

print(f"✓ Saved annotated document to: {jsonl_path}")

LangExtract: Saving to DELL_8K_20251228_100308.jsonl: 1 docs [00:00, 854.06 docs/s]

✓ Saved 1 documents to DELL_8K_20251228_100308.jsonl
✓ Saved annotated document to: /home/faisal/EventMarketDB/drivers/8K_XBRL_Linking/output/DELL_8K_20251228_100308.jsonl


In [14]:
# Generate interactive HTML visualization
html_path = os.path.join(OUTPUT_DIR, f"{base_name}.html")

# Use LangExtract's visualize - can take AnnotatedDocument directly
html_content = lx.visualize(annotated_doc)

# Save HTML file
with open(html_path, "w") as f:
    if hasattr(html_content, 'data'):
        f.write(html_content.data)
    else:
        f.write(str(html_content))

print(f"✓ Saved HTML visualization to: {html_path}")
print(f"\nOpen in browser to view extractions highlighted in source text.")

✓ Saved HTML visualization to: /home/faisal/EventMarketDB/drivers/8K_XBRL_Linking/output/DELL_8K_20251228_100308.html

Open in browser to view extractions highlighted in source text.


In [15]:
stop

NameError: name 'stop' is not defined